# Analisis generarl de la serie de tiempo
Se crea una rutina de reportes para poder visualizar el estado de la serie temporal, la idea es comenzar desde el analisis general de la serie hasta el analisis especifico como analisis mensual y diario.
Con esto se pretende generar una serie de metricas para determinar que metodos de intermpolacion podemos utilizar para la imputacion de datos ausentes.

In [1]:
# Configuración del registro de logs
import logging
import numpy as np
import pandas as pd
from utils.utils import normalize_series, reshample_time_serie, categorize_precipitation
from graphics_utils.go import multi_line
from api_somo import DataFetcher

logging.basicConfig(level=logging.INFO)
logger = logging.getLogger(__name__)

# URL de la API y parámetros de consulta
api_url = "http://127.0.0.1:8000/database/filter-serie/"
params = {
    "station_name": "tumaco",
    "variable_name": "Precipitación acumulada",
    "processing_level_name": "Control de calidad",
    "start_date": "2010-01-01",
    "end_date": "2010-12-31"
}

try:
    # 1. Fetch and process the data
    logger.info("Fetching data from the API...")
    historical_series = DataFetcher.fetch_and_process_data(api_url, params)

    if historical_series.empty:
        raise ValueError("The historical series is empty.")

    logger.info(f"Fetched historical series: {historical_series.head()}")

    # 2. Limpieza de datos
    logger.info("Cleaning data...")
    historical_series.loc[historical_series['qf'] == 9, 'value'] = np.nan
    registros_nan = historical_series[historical_series['value'].isna()]  # Registros con valores NaN

    # 3. Remuestreo
    logger.info("Resampling data...")
    serie_historica_resample = reshample_time_serie(historical_series, 'ME', 'sum')

    # 4. Categorización
    logger.info("Categorizing precipitation data...")
    historical_series = categorize_precipitation(historical_series, params)

    # 5. Normalización
    logger.info("Normalizing data...")
    historical_series['normalized_value'] = normalize_series(
        historical_series['value'], method='min-max'
    )
    serie_historica_resample['normalized_value'] = normalize_series(
        serie_historica_resample['value'], method='min-max'
    )

    # 6. Filtrar valores nulos o cero
    logger.info("Filtering out zero values...")
    serie_historica = historical_series[historical_series['value'] != 0]

    # 7. Visualización
    logger.info("Visualizing data...")
    series_fig = multi_line(
        original=historical_series['value'],
        normalizada=serie_historica_resample['value']
    )
    series_fig.show()

    # 8. Estadísticas descriptivas
    logger.info("Calculating descriptive statistics...")
    logger.info("Descriptive statistics for original values:")
    print(historical_series['value'].describe())
    logger.info("Descriptive statistics for resampled values:")
    print(serie_historica_resample['value'].describe())

    # 9. Mostrar registros con valores NaN
    if not registros_nan.empty:
        logger.info("Displaying records with NaN values...")
        print("Registros con valores NaN:")
        print(registros_nan)

except ValueError as ve:
    logger.error(f"ValueError: {ve}")
except Exception as e:
    logger.error(f"Unexpected error occurred: {e}")


INFO:__main__:Fetching data from the API...
INFO:api_somo:Sending request to http://127.0.0.1:8000/database/filter-serie/ with parameters: {'station_name': 'tumaco', 'variable_name': 'Precipitación acumulada', 'processing_level_name': 'Control de calidad', 'start_date': '2010-01-01', 'end_date': '2010-12-31'}
INFO:api_somo:Original columns: ['date_time', 'sensor_data', 'quality_flag']
INFO:api_somo:Columns after renaming: ['timestamp', 'value', 'qf']
INFO:api_somo:Timestamp conversion and indexing complete.
INFO:__main__:Fetched historical series:                            value  qf
timestamp                           
2010-01-01 05:00:00+00:00    0.0   1
2010-01-01 05:10:00+00:00    0.0   1
2010-01-01 05:20:00+00:00    0.0   1
2010-01-01 05:30:00+00:00    0.0   1
2010-01-01 05:40:00+00:00    0.0   1
INFO:__main__:Cleaning data...
INFO:__main__:Resampling data...
INFO:__main__:Categorizing precipitation data...
INFO:__main__:Normalizing data...
INFO:__main__:Filtering out zero values.

INFO:__main__:Calculating descriptive statistics...
INFO:__main__:Descriptive statistics for original values:
INFO:__main__:Descriptive statistics for resampled values:
INFO:__main__:Displaying records with NaN values...


count    50700.000000
mean         0.063030
std          0.452372
min          0.000000
25%          0.000000
50%          0.000000
75%          0.000000
max         16.700000
Name: value, dtype: float64
count     12.000000
mean     266.300000
std      175.520877
min       26.100000
25%      155.425000
50%      225.350000
75%      358.075000
max      592.100000
Name: value, dtype: float64
Registros con valores NaN:
                           value  qf
timestamp                           
2010-01-31 05:10:00+00:00    NaN   9
2010-01-31 05:20:00+00:00    NaN   9
2010-01-31 05:30:00+00:00    NaN   9
2010-01-31 05:40:00+00:00    NaN   9
2010-01-31 05:50:00+00:00    NaN   9
...                          ...  ..
2010-12-19 04:20:00+00:00    NaN   9
2010-12-19 04:30:00+00:00    NaN   9
2010-12-19 04:40:00+00:00    NaN   9
2010-12-19 04:50:00+00:00    NaN   9
2010-12-19 05:00:00+00:00    NaN   9

[1717 rows x 2 columns]


---
# Analisis de la calidad de la serie Historica
En este grafico podemos ver el total de datos agrupados por calidad en cada mes, es decir si una serie tiene 15 años tiene 15 eneros, 15 noviembres etc, con esta grafica podemos ver a modo general con cuantos datos del total contamos para la recuperacion de la serie y los datos faltantes, esta grafica es muy importante porque nos da  un marcador de calidad historico por meses, incluso aqui se puede analizar si la perdida de datos es sistematica o si tiene algun comportamiento con correlacion temporal.

In [2]:
from graphics_utils.express import fig_pie_month
from graphics_utils.go import multi_line, multi_boxplot


print('Serie original')
pie_fig = fig_pie_month(historical_series, params)
pie_fig.show()
print('serie_remuestreada')
pie_fig = fig_pie_month(serie_historica_resample, params)
pie_fig.show()
boxplot_fig = multi_line(historical_series=historical_series['value'], serie_remuestreada=serie_historica_resample['value'])
boxplot_fig.show()
original_line = multi_line(Original=historical_series['normalized_value'], remuestreada=serie_historica_resample['normalized_value'])
original_line.show()
'''boxplot_fig = fig_boxplot(historical_series, params, color='month')
boxplot_fig.show()
boxplot_fig = fig_boxplot(serie_historica_resample, params, color='month')
boxplot_fig.show()'''

Serie original


serie_remuestreada


"boxplot_fig = fig_boxplot(historical_series, params, color='month')\nboxplot_fig.show()\nboxplot_fig = fig_boxplot(serie_historica_resample, params, color='month')\nboxplot_fig.show()"

# Redes neuronales recurentes

1. Preparar los datos
- Asegúrate de que los datos estén normalizados o estandarizados si las variables tienen diferentes escalas.

In [3]:
'''import numpy as np
import pandas as pd
from sklearn.metrics import r2_score
import matplotlib.pyplot as plt
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import LSTM, Dense
from sklearn.model_selection import train_test_split
from graphics_utils.go import multi_line  # Asegúrate de que `graphics_utils.go` esté correctamente importado

# Reemplazar valores de calidad (qf == 9) con NaN
historical_series.loc[historical_series['qf'] == 9, 'value'] = np.nan
datos = historical_series[['value']].copy()

# Crear una columna con el valor retrasado (lag)
datos['value_lag'] = datos['value'].shift(20)

# Eliminar filas con NaN en 'value' o 'value_lag' para entrenar el modelo
datos_entrenamiento = datos.dropna()

# Preprocesar los datos para la red neuronal
# Definir las variables X e Y
X = datos_entrenamiento[['value_lag']].values
y = datos_entrenamiento['value'].values

# Reshape de X para que sea compatible con el LSTM (n_samples, n_timesteps, n_features)
X = X.reshape((X.shape[0], 1, X.shape[1]))

# Dividir los datos en conjunto de entrenamiento y validación
X_train, X_val, y_train, y_val = train_test_split(X, y, test_size=0.2, random_state=42)

# Crear el modelo LSTM
modelo = Sequential()
modelo.add(LSTM(50, activation='relu', input_shape=(X_train.shape[1], X_train.shape[2])))
modelo.add(Dense(1))  # Una salida (valor imputado)
modelo.compile(optimizer='adam', loss='mean_squared_error')

# Entrenar el modelo
modelo.fit(X_train, y_train, epochs=50, batch_size=32, validation_data=(X_val, y_val))

# Realizar predicciones sobre el conjunto de validación
y_pred = modelo.predict(X_val)

# Coeficiente de determinación (R²)
r2 = r2_score(y_val, y_pred)
print('Coeficiente de determinación (R²): ', round(r2, 2))

# Filtrar las filas donde 'value' es NaN y 'value_lag' no es NaN para imputar valores
datos_faltantes = datos.loc[datos['value'].isna() & datos['value_lag'].notna(), 'value_lag']

# Predecir los valores faltantes usando el modelo
X_faltantes = datos_faltantes.values.reshape((-1, 1, 1))  # Asegurarse de que tiene la forma correcta
datos.loc[datos_faltantes.index, 'value_imputed'] = modelo.predict(X_faltantes)

# Asegurar que 'value_imputed' esté completa (sin NaN)
datos['value_imputed'].fillna(datos['value'], inplace=True)

# Imprimir el DataFrame para ver resultados
print(datos)

# Visualizar los resultados con multi_line
fig = multi_line(CCCP=datos['value'], Imputadas=datos['value_imputed'])
fig.show()
'''

"import numpy as np\nimport pandas as pd\nfrom sklearn.metrics import r2_score\nimport matplotlib.pyplot as plt\nfrom tensorflow.keras.models import Sequential\nfrom tensorflow.keras.layers import LSTM, Dense\nfrom sklearn.model_selection import train_test_split\nfrom graphics_utils.go import multi_line  # Asegúrate de que `graphics_utils.go` esté correctamente importado\n\n# Reemplazar valores de calidad (qf == 9) con NaN\nhistorical_series.loc[historical_series['qf'] == 9, 'value'] = np.nan\ndatos = historical_series[['value']].copy()\n\n# Crear una columna con el valor retrasado (lag)\ndatos['value_lag'] = datos['value'].shift(20)\n\n# Eliminar filas con NaN en 'value' o 'value_lag' para entrenar el modelo\ndatos_entrenamiento = datos.dropna()\n\n# Preprocesar los datos para la red neuronal\n# Definir las variables X e Y\nX = datos_entrenamiento[['value_lag']].values\ny = datos_entrenamiento['value'].values\n\n# Reshape de X para que sea compatible con el LSTM (n_samples, n_timestep

---
## Imputación con KNN
Imputar datos faltantes utilizando los k vecinos más cercanos (k-nearest neighbors, KNN) es una técnica común y efectiva, especialmente para conjuntos de datos en los que los valores tienen una correlación espacial, temporal o de características entre ellos.

In [4]:
'''historical_series.loc[historical_series['qf'] != 1, 'value'] = np.nan

from sklearn.impute import KNNImputer

# Configurar el imputador con KNN
imputer = KNNImputer(n_neighbors=5, weights='uniform', metric='nan_euclidean')

# Realizar la imputación solo en la columna 'values' y mantener el índice 'timestamp'
serie_historica_impitada=historical_series.copy()
serie_historica_impitada['value'] = imputer.fit_transform(serie_historica_impitada[['value']])


from graphics_utils.go import multi_line
fig = multi_line(CCCP=serie_historica['value'], Imputadas=serie_historica_impitada['value'])
fig.show()
'''

"historical_series.loc[historical_series['qf'] != 1, 'value'] = np.nan\n\nfrom sklearn.impute import KNNImputer\n\n# Configurar el imputador con KNN\nimputer = KNNImputer(n_neighbors=5, weights='uniform', metric='nan_euclidean')\n\n# Realizar la imputación solo en la columna 'values' y mantener el índice 'timestamp'\nserie_historica_impitada=historical_series.copy()\nserie_historica_impitada['value'] = imputer.fit_transform(serie_historica_impitada[['value']])\n\n\nfrom graphics_utils.go import multi_line\nfig = multi_line(CCCP=serie_historica['value'], Imputadas=serie_historica_impitada['value'])\nfig.show()\n"

# Descomponer la serie temporal
Esta seccion se crea para hacer el procesamiento de descomposicion

In [5]:
'''import numpy as np
import pandas as pd
from statsmodels.tsa.statespace.sarimax import SARIMAX
from sklearn.metrics import mean_squared_error
from graphics_utils.go import multi_line  # Asegúrate de importar correctamente tu función

# Reemplazar valores de calidad (qf == 9) con NaN
historical_series.loc[historical_series['qf'] == 9, 'value'] = np.nan

# Resample de la serie de tiempo y rellenar valores faltantes iniciales con interpolación básica
datos = historical_series.resample('h').sum()

# Parámetros SARIMA
p, d, q = 1, 2, 1
P, D, Q, S = 1, 1, 1, 24

# Ajustar el modelo SARIMA
modelo_sarima = SARIMAX(datos['value'], order=(p, d, q), seasonal_order=(P, D, Q, S))
modelo_ajustado = modelo_sarima.fit(disp=False)

# Predecir valores (incluyendo los NaN)
# Asegurar que las predicciones no sean negativas
predicciones = modelo_ajustado.predict(start=0, end=len(datos) - 1)
predicciones[predicciones < 0] = 0


# Crear la serie imputada
serie_imputada = datos['value'].copy()
nan_indices = datos['value'].isna()  # Índices con NaN en la serie original
serie_imputada[nan_indices] = predicciones[nan_indices]  # Rellenar NaN con predicciones

# Calcular RMSE entre los valores reales (sin NaN) y las predicciones
rmse = np.sqrt(mean_squared_error(datos['value'].dropna(), predicciones[~nan_indices]))
print(f"RMSE entre los valores reales e imputados: {rmse:.2f}")

# Agregar las series al DataFrame original para visualización
datos['value_forecast'] = predicciones  # Serie de pronóstico
datos['value_imputed'] = serie_imputada  # Serie imputada combinada

# Visualizar las tres series con multi_line
fig = multi_line(
    Original=datos['value'],
    Pronóstico=datos['value_forecast'],
    Imputadas=datos['value_imputed']
)
fig.show()

# Imprimir el DataFrame con las tres series
print(datos)'''


'import numpy as np\nimport pandas as pd\nfrom statsmodels.tsa.statespace.sarimax import SARIMAX\nfrom sklearn.metrics import mean_squared_error\nfrom graphics_utils.go import multi_line  # Asegúrate de importar correctamente tu función\n\n# Reemplazar valores de calidad (qf == 9) con NaN\nhistorical_series.loc[historical_series[\'qf\'] == 9, \'value\'] = np.nan\n\n# Resample de la serie de tiempo y rellenar valores faltantes iniciales con interpolación básica\ndatos = historical_series.resample(\'h\').sum()\n\n# Parámetros SARIMA\np, d, q = 1, 2, 1\nP, D, Q, S = 1, 1, 1, 24\n\n# Ajustar el modelo SARIMA\nmodelo_sarima = SARIMAX(datos[\'value\'], order=(p, d, q), seasonal_order=(P, D, Q, S))\nmodelo_ajustado = modelo_sarima.fit(disp=False)\n\n# Predecir valores (incluyendo los NaN)\n# Asegurar que las predicciones no sean negativas\npredicciones = modelo_ajustado.predict(start=0, end=len(datos) - 1)\npredicciones[predicciones < 0] = 0\n\n\n# Crear la serie imputada\nserie_imputada = da